In [13]:
!pip install geopy

     |████████████████████████████████| 112 kB 4.8 MB/s eta 0:00:01
  Using cached geographiclib-1.50-py3-none-any.whl (38 kB)


In [14]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import datetime as dt
from datetime import datetime
import folium
import folium.plugins as plugins
from sklearn.cluster import KMeans
import seaborn as sns; sns.set()
import geopy.distance
import math

In [15]:
# Show more rows when printing lists
pd.options.display.max_rows = 50

## Methods

### Load file

In [16]:
#get DateTime on the correct format (in accordance with excel file)
def load_file(file_name):
    df = pd.read_csv(file_name)
    
    # change date format
    df['DateTime'] = pd.TimedeltaIndex(df['DateTime'], unit='d') + dt.datetime(1899,12,30)
    
    # reformat coordinates to dot-separated floats
    df['Long'] = df['Long'].apply(lambda x: float(str(x).replace(',','.')))
    df['Lat'] = df['Lat'].apply(lambda x: float(str(x).replace(',','.')))
    
    # remove outliers
    #df = df[(df['Long'] <= 11) & (df['Long'] >= 10.62)]
    # only keep trip if it has a start and an end
    df = df[df.duplicated('Trip ID', keep=False)]
    return df

### Remove incomplete trips

In [17]:
def remove_incomplete_trips(df):
    df = df[df.duplicated('Trip ID', keep=False)]
    return df

### Get start and end data

In [18]:
def get_start_data(df):
    return df.loc[df['TripStage'] == 'Start']

def get_end_data(df):
    return df.loc[df['TripStage'] == 'End']

### Scatter plot

In [19]:
def plot_scatter(df, n, m):
    blue = 0
    red = 0
    # mark each station as a point
    for index, row in df.sample(n=n).iterrows():
        folium.CircleMarker([row['Lat'], row['Long']],
                            radius=3,
                            popup = "Type: " + str(row['TripStage']) + "\nTime: "+str(row['DateTime'])+"\nDuration: "+str(row['Trip duration (min)'])
                            +"\nTripID: "+str(row['Trip ID'])+"\nZone: "+str(row['Zone']),
                            fill = True,
                            color= "#3db7e4" if row['TripStage'] == "Start" else "#e43d43", # divvy color
                           ).add_to(m)
        if (row['TripStage'] == "Start"):
            blue += 1
        else:
            red += 1

    return m, blue, red

### Grid creator (returns polygons as geojson objects in a list)

In [20]:
#https://www.jpytr.com/post/analysinggeographicdatawithfolium/
def get_geojson_grid(upper_right, lower_left, lat_dim=8, lon_dim=15):
    """Returns a grid of geojson rectangles, and computes the exposure in each section of the grid based on the vessel data.

    Parameters
    ----------
    upper_right: array_like
        The upper right hand corner of "grid of grids" (the default is the upper right hand [lat, lon] of the USA).

    lower_left: array_like
        The lower left hand corner of "grid of grids"  (the default is the lower left hand [lat, lon] of the USA).

    n: integer
        The number of rows/columns in the (n,n) grid.

    Returns
    -------

    list
        List of "geojson style" dictionary objects   
    """

    all_boxes = []

    lat_steps = np.linspace(lower_left[0], upper_right[0], lat_dim+1)
    lon_steps = np.linspace(lower_left[1], upper_right[1], lon_dim+1)

    lat_stride = lat_steps[1] - lat_steps[0]
    lon_stride = lon_steps[1] - lon_steps[0]
    
    zone_counter = 1

    for lat in lat_steps[:-1]:
        for lon in lon_steps[:-1]:
           
            
            # Define dimensions of box in grid
            upper_left = [lon, lat + lat_stride]
            upper_right = [lon + lon_stride, lat + lat_stride]
            lower_right = [lon + lon_stride, lat]
            lower_left = [lon, lat]
                

            # Define json coordinates for polygon
            coordinates = [
                upper_left,
                upper_right,
                lower_right,
                lower_left,
                upper_left
            ]

            geo_json = {"type": "FeatureCollection",
                        "properties":{
                            "lower_left": lower_left,
                            "upper_right": upper_right,
                        },
                        "features":[],
                        "Number": zone_counter}


            grid_feature = {
                "type":"Feature",
                "geometry":{
                    "type":"Polygon",
                    "coordinates": [coordinates],
                }
            }

            geo_json["features"].append(grid_feature)

            all_boxes.append(geo_json)
            
            zone_counter+=1

    return all_boxes

### Plot n samples on the predefined grid

In [21]:
def plot_samples_on_grid(dataframe, n, excluded_zones):
    
    lower_left = [59.855331, 10.601628]
    upper_right = [59.973287, 10.950989]
    
    
    center = [lower_left[0]+(upper_right[0]-lower_left[0])/2,lower_left[1]+(upper_right[1]-lower_left[1])/2]

    #grid_size = int(np.sqrt(len(world.pNodes)))
    grid_size = (26,40)
    
    map = folium.Map(center, zoom_start = 10.8)
    

    grid = get_geojson_grid(lower_left, upper_right , lat_dim=grid_size[0], lon_dim=grid_size[1])
    
    count = 1
    for i, geo_json in enumerate(grid):
        if (str(len(grid)-i) not in excluded_zones):
            gj = folium.GeoJson(geo_json,
                    style_function=lambda feature: {#'fillColor': color,
                                                    'color':'#df80e8',
                                                    'weight': 2,
                                                    'dashArray': '5, 5',
                                                    'fillOpacity': 0.1}).add_to(map)
            popup_string = "Zone "+str(count)
            count += 1
            gj.add_child(folium.Popup(popup_string, max_width=400))

    map, start, end = plot_scatter(dataframe, n, map) 
    print("Start/End percentages: " + str((start/(start+end))*100) + "%/" + str((end/(start+end))*100)
            + "%")
    display(map)

### Take data as input, return the data that satisfies the time criteria

In [22]:
def hour_selector(data, hour_start, hour_end, include_weekends=False):
    if (hour_start == 0 and hour_end == 24):
        return data
    elif (hour_start > 24 or hour_start < 0 or hour_end > 24 or hour_end < 0):
        print("Invalid times")
        return
    elif (hour_start >= hour_end):
        print("Invalid times")
        return
    elif (hour_start != math.floor(hour_start)):
        print("Only whole hours permitted")
        return
    else:
        data_copy = data.copy()
        mask = (data_copy['DateTime'].dt.hour >= hour_start) & (data_copy['DateTime'].dt.hour <= (hour_end - 1))
        data_copy = data_copy.loc[mask]
        if ~include_weekends:
            mask = ((data_copy['DateTime'].dt.weekday != 5) & (data_copy['DateTime'].dt.weekday != 6))
            data_copy = data_copy.loc[mask]
        return data_copy
    
    
    

## Assign zone to each row, remove trips outside zones

In [24]:
file_name = "../../data/2019_vy.csv"

list_zones = []
for zone in range(254):
    line = []
    line.append(zone+1)
    line.append(np.nan)
    line.append(np.nan)
    line.append(np.nan)
    list_zones.append(line)
    

zone_data = pd.DataFrame(list_zones, columns = ['Zone', 'Lower Left', 'Upper Right', 'Center'])

#Size of zone area
lower_left = [59.855331, 10.601628]
upper_right = [59.973287, 10.950989]
center = [lower_left[0]+(upper_right[0]-lower_left[0])/2,lower_left[1]+(upper_right[1]-lower_left[1])/2]

data = load_file(file_name)
data_copy = data.copy()

#Start data and end data
start_data = get_start_data(data_copy)
end_data = get_end_data(data_copy)

excluded_zones = []

#List of polygons in grid
zones = get_geojson_grid(upper_right, lower_left, lat_dim=26, lon_dim=40)

# For each zone, mark all trips in that zone with the zone number
for zone in zones:
    upper_left = zone['features'][0]['geometry']['coordinates'][0][0]    
    upper_right = zone['features'][0]['geometry']['coordinates'][0][1]    
    lower_right = zone['features'][0]['geometry']['coordinates'][0][2]    
    lower_left = zone['features'][0]['geometry']['coordinates'][0][3]
    
    
    data_copy.loc[
        (data_copy.Long < float(upper_right[0]))
        & (data_copy.Long > float(upper_left[0]))
        & (data_copy.Lat > float(lower_left[1]))
        & (data_copy.Lat < float(upper_left[1])),'Zone'] = str(zone['Number']).strip()

    
    # Calculate new field "No. trips zone", which indicates how many starts and ends that have happened in that zone 
    data_copy.loc[
        data_copy.Zone == str(zone['Number']).strip(), 'No. trips zone'] = len(data_copy.loc[data_copy.Zone == str(zone['Number']).strip()])
    
    # add zones with less than x visits to excluded zones
    if (len(data_copy.loc[data_copy.Zone == str(zone['Number']).strip()]) <= 150):
        excluded_zones.append(str(zone['Number']).strip())

# Rename zone field in data to match that of the plot
counter = len(zones)-len(excluded_zones)
for zone in zones:
    if (str(zone['Number']) not in excluded_zones):
        data_copy.loc[data_copy.Zone == str(zone['Number']).strip(), 'Zone'] = counter
        
        zone_data.loc[(zone_data.Zone == counter),'Lower Left'] = str(zone['properties']['lower_left'])
        zone_data.loc[(zone_data.Zone == counter),'Upper Right'] = str(zone['properties']['upper_right'])
        lat_center = (zone['properties']['upper_right'][0] - zone['properties']['lower_left'][0])/2 + zone['properties']['lower_left'][0]
        long_center = (zone['properties']['upper_right'][1] - zone['properties']['lower_left'][1])/2 + zone['properties']['lower_left'][1]
        center_coord = [lat_center, long_center]
        zone_data.loc[(zone_data.Zone == counter),'Center'] = str(center_coord)
        counter -= 1
        
        
        
        
# remove starts and ends that happened outside of the included zones       
data_copy = data_copy[(~data_copy['Zone'].isin(excluded_zones)) & (~data_copy['Zone'].empty)]
        
# remove incomplete trips, so that the the system becomes "closed", 
# meaning that all starts and ends happen within the defined area
data_copy = remove_incomplete_trips(data_copy)
        

In [25]:
zone_data.head(42)

Zone                                Lower Left  \
0      1          [10.79377655, 59.96421346153846]   
1      2         [10.785042525, 59.96421346153846]   
2      3   [10.776308499999999, 59.96421346153846]   
3      4         [10.767574475, 59.96421346153846]   
4      5          [10.75884045, 59.96421346153846]   
5      6         [10.750106425, 59.96421346153846]   
6      7         [10.732638375, 59.96421346153846]   
7      8          [10.72390435, 59.96421346153846]   
8      9          [10.79377655, 59.95967669230769]   
9     10         [10.785042525, 59.95967669230769]   
10    11   [10.776308499999999, 59.95967669230769]   
11    12          [10.75884045, 59.95967669230769]   
12    13         [10.750106425, 59.95967669230769]   
13    14           [10.7413724, 59.95967669230769]   
14    15         [10.732638375, 59.95967669230769]   
15    16          [10.72390435, 59.95967669230769]   
16    17          [10.79377655, 59.95513992307692]   
17    18         [10.785042525, 59.95513992307692]   
18    19   [10.776308499999999, 59.95513992307692]   
19    20          [10.75884045, 59.95513992307692]   
20    21         [10.750106425, 59.95513992307692]   
21    22           [10.7413724, 59.95513992307692]   
22    23         [10.732638375, 59.95513992307692]   
23    24          [10.72390435, 59.95513992307692]   
24    25   [10.715170324999999, 59.95513992307692]   
25    26          [10.79377655, 59.95060315384615]   
26    27         [10.785042525, 59.95060315384615]   
27    28   [10.776308499999999, 59.95060315384615]   
28    29         [10.767574475, 59.95060315384615]   
29    30          [10.75884045, 59.95060315384615]   
30    31         [10.750106425, 59.95060315384615]   
31    32           [10.7413724, 59.95060315384615]   
32    33         [10.732638375, 59.95060315384615]   
33    34          [10.72390435, 59.95060315384615]   
34    35   [10.715170324999999, 59.95060315384615]   
35    36        [10.802510575, 59.946066384615385]   
36    37         [10.79377655, 59.946066384615385]   
37    38        [10.785042525, 59.946066384615385]   
38    39  [10.776308499999999, 59.946066384615385]   
39    40        [10.767574475, 59.946066384615385]   
40    41         [10.75884045, 59.946066384615385]   
41    42        [10.750106425, 59.946066384615385]   

                                 Upper Right  \
0    [10.802510575000001, 59.96875023076923]   
1           [10.79377655, 59.96875023076923]   
2          [10.785042525, 59.96875023076923]   
3            [10.7763085, 59.96875023076923]   
4          [10.767574475, 59.96875023076923]   
5    [10.758840450000001, 59.96875023076923]   
6    [10.741372400000001, 59.96875023076923]   
7          [10.732638375, 59.96875023076923]   
8   [10.802510575000001, 59.964213461538456]   
9          [10.79377655, 59.964213461538456]   
10        [10.785042525, 59.964213461538456]   
11        [10.767574475, 59.964213461538456]   
12  [10.758840450000001, 59.964213461538456]   
13        [10.750106425, 59.964213461538456]   
14  [10.741372400000001, 59.964213461538456]   
15        [10.732638375, 59.964213461538456]   
16   [10.802510575000001, 59.95967669230769]   
17          [10.79377655, 59.95967669230769]   
18         [10.785042525, 59.95967669230769]   
19         [10.767574475, 59.95967669230769]   
20   [10.758840450000001, 59.95967669230769]   
21         [10.750106425, 59.95967669230769]   
22   [10.741372400000001, 59.95967669230769]   
23         [10.732638375, 59.95967669230769]   
24          [10.72390435, 59.95967669230769]   
25   [10.802510575000001, 59.95513992307692]   
26          [10.79377655, 59.95513992307692]   
27         [10.785042525, 59.95513992307692]   
28           [10.7763085, 59.95513992307692]   
29         [10.767574475, 59.95513992307692]   
30   [10.758840450000001, 59.95513992307692]   
31         [10.750106425, 59.95513992307692]   
32   [10.741372400000001, 59.95513992307692]   
33         [10.732638375, 59.95513992307692]   
3

In [26]:
#zone_data.to_csv("./data/zone_coordinates.csv")

In [27]:
#Sone 190 - Vika p-hus - 3 ladeplasser
#Sone 191 - Aker brygge p-hus - Ukjent antall ladeplasser, antar 10
#Sone 204 - Aker Fornebuporten - 4 ladeplasser
#Sone 189 - Paleet p-hus - 10 ladeplasser
#Sone 41 - Nydael Torgbygget p-hus - 4 ladeplasser
#Sone 146 - Vulkan p-hus - 8 ladeplasser

charging_zones = [[41,4],[146,8],[189,10],[190,3],[191,10],[204,4]]
charging_data = pd.DataFrame(charging_zones, columns = ['Zone', 'Nr of charging stations'])

charging_data['Lower Left'] = np.nan
charging_data['Upper Right'] = np.nan
charging_data['Center'] = np.nan


In [29]:
charging_data.iloc[0,2] = str(zone_data.loc[(zone_data['Zone'] == 41), 'Lower Left'])[3:39]
charging_data.iloc[0,3] = str(zone_data.loc[(zone_data['Zone'] == 41), 'Upper Right'])[3:39]
charging_data.iloc[0,4] = str(zone_data.loc[(zone_data['Zone'] == 41), 'Center'])[3:45]
charging_data.iloc[1,2] = str(zone_data.loc[(zone_data['Zone'] == 146), 'Lower Left'])[3:40]
charging_data.iloc[1,3] = str(zone_data.loc[(zone_data['Zone'] == 146), 'Upper Right'])[3:46]
charging_data.iloc[1,4] = str(zone_data.loc[(zone_data['Zone'] == 146), 'Center'])[3:42]
charging_data.iloc[2,2] = str(zone_data.loc[(zone_data['Zone'] == 189), 'Lower Left'])[3:38]
charging_data.iloc[2,3] = str(zone_data.loc[(zone_data['Zone'] == 189), 'Upper Right'])[3:41]
charging_data.iloc[2,4] = str(zone_data.loc[(zone_data['Zone'] == 189), 'Center'])[3:41]
charging_data.iloc[3,2] = str(zone_data.loc[(zone_data['Zone'] == 190), 'Lower Left'])[3:39]
charging_data.iloc[3,3] = str(zone_data.loc[(zone_data['Zone'] == 190), 'Upper Right'])[3:41]
charging_data.iloc[3,4] = str(zone_data.loc[(zone_data['Zone'] == 190), 'Center'])[3:41]
charging_data.iloc[4,2] = str(zone_data.loc[(zone_data['Zone'] == 191), 'Lower Left'])[3:46]
charging_data.iloc[4,3] = str(zone_data.loc[(zone_data['Zone'] == 191), 'Upper Right'])[3:40]
charging_data.iloc[4,4] = str(zone_data.loc[(zone_data['Zone'] == 191), 'Center'])[3:41]
charging_data.iloc[5,2] = str(zone_data.loc[(zone_data['Zone'] == 204), 'Lower Left'])[3:39]
charging_data.iloc[5,3] = str(zone_data.loc[(zone_data['Zone'] == 204), 'Upper Right'])[3:40]
charging_data.iloc[5,4] = str(zone_data.loc[(zone_data['Zone'] == 204), 'Center'])[3:42]




charging_data.to_csv("../../data/charging_zones.csv")
charging_data.head(10)

Zone  Nr of charging stations                                   Lower Left  \
0    41                        4            [10.75884045, 59.946066384615385]   
1   146                        8            [10.750106425, 59.91884576923077]   
2   189                       10              [10.7413724, 59.90977223076923]   
3   190                        3             [10.72390435, 59.90977223076923]   
4   191                       10      [10.715170324999999, 59.90977223076923]   
5   204                        4             [10.61909605, 59.90523546153846]   

                                   Upper Right  \
0            [10.767574475, 59.95060315384615]   
1      [10.758840450000001, 59.92338253846154]   
2           [10.750106425, 59.914308999999996]   
3           [10.732638375, 59.914308999999996]   
4            [10.72390435, 59.914308999999996]   
5            [10.627830075, 59.90977223076923]   

                                       Center  
0     [10.763207462499999, 59.94833476923077]  
1         [10.7544734375, 59.921114153846155]  
2          [10.7457394125, 59.91204061538461]  
3          [10.7282713625, 59.91204061538461]  
4          [10.7195373375, 59.91204061538461]  
5         [10.6234630625, 59.907503846153844]

In [30]:
print("Nr of excluded zones: " + str(len(excluded_zones)))
print("Nr of included zones: " + str(str(1040-len(excluded_zones))))

Nr of excluded zones: 786
Nr of included zones: 254


In [31]:
#nr of cars
print("Nr of cars in the system: " + str(data_copy['Car ID'].nunique()))

#Number of trips
count_new = len(data_copy.index)/2
count_old = len(data.index)/2
print("Number of trips in the system: " + str(count_new))
print("Number of trips in the original data: " + str(count_old))

Nr of cars in the system: 255
Number of trips in the system: 146198.0
Number of trips in the original data: 149405.0


## Plot scatter plot

In [32]:
lower_left = [59.855331, 10.601628]
upper_right = [59.973287, 10.950989]
center = [lower_left[0]+(upper_right[0]-lower_left[0])/2,lower_left[1]+(upper_right[1]-lower_left[1])/2]
map = folium.Map(center, zoom_start = 10.8)

plot_scatter(data_copy, 1000, map)

(<folium.folium.Map at 0x7fbfda7cfd90>, 511, 489)

## Plot n samples on grid 

In [33]:
data_new = hour_selector(data_copy,2,5)

In [34]:
plot_samples_on_grid(data_new,2700, excluded_zones)

Start/End percentages: 48.74074074074074%/51.25925925925926%
